In [6]:
import pandas as pd 

df = pd.read_excel('Desarrollos Ags Mayo 2025.xlsx')
df.columns

Index(['Desarrollo', 'Desarrollador', 'Unidad + se vende',
       'Ventas mensuales históricas', 'Ventas mensuales Feb25',
       '# meses en venta', 'Oferta disponible anterior',
       'Oferta disponible actual', 'Oferta vendida', 'Oferta total',
       '% de vendido', 'Tamaño prom. terreno m2', 'Tamaño prom. constr. m2',
       'Precio prom. m2 terreno', 'Precio prom.  m2 constr.',
       'Tipo de proyecto', 'Zona', 'Precio m2', 'm2', 'Latitud', 'Longitud'],
      dtype='object')

In [9]:
# pip install folium
import folium
from folium.plugins import MarkerCluster
import pandas as pd
import numpy as np

# ==== 1) Copia y renombra la columna antes del mapa ====
df = df.copy()
df = df.rename(columns={"Ventas mensuales Feb25": "Ventas mensuales Mayo25"})

# ==== 2) Función para generar el mapa ====
def make_folium_map(df, archivo_html="mapa_desarrollos.html"):
    d = df.copy()
    d = d.replace([np.inf, -np.inf], np.nan)
    d = d.dropna(subset=["Latitud", "Longitud"])

    # Centro del mapa
    lat_c = d["Latitud"].astype(float).mean()
    lon_c = d["Longitud"].astype(float).mean()

    m = folium.Map(location=[lat_c, lon_c], zoom_start=11, tiles="CartoDB positron")

    # Colores por Zona
    zonas = d["Zona"].astype(str).unique().tolist()
    base_colors = [
        "#1f77b4", "#ff7f0e", "#2ca02c", "#d62728",
        "#9467bd", "#8c564b", "#e377c2", "#7f7f7f",
        "#bcbd22", "#17becf"
    ]
    color_by_zona = {z: base_colors[i % len(base_colors)] for i, z in enumerate(zonas)}

    cluster = MarkerCluster().add_to(m)

    for _, r in d.iterrows():
        lat = float(r["Latitud"])
        lon = float(r["Longitud"])
        zona = str(r.get("Zona", "—"))
        desarrollo = str(r.get("Desarrollo", "—"))
        desarrollador = str(r.get("Desarrollador", "—"))
        precio_m2 = r.get("Precio m2", None)
        m2 = r.get("m2", None)
        ventas_mayo25 = r.get("Ventas mensuales Mayo25", None)

        # --- Formateos ---
        ventas_txt = f"{float(ventas_mayo25):.1f}" if pd.notna(ventas_mayo25) else "—"
        precio_txt = f"${float(precio_m2):,.0f} / m²" if pd.notna(precio_m2) else "—"
        m2_txt = f"{float(m2):.0f}" if pd.notna(m2) else "—"

        popup_html = f"""
        <b>{desarrollo}</b><br>
        Desarrollador: {desarrollador}<br>
        Zona: {zona}<br>
        Ventas mensuales Mayo25: {ventas_txt}<br>
        Precio: {precio_txt}<br>
        m² construcción (o lote): {m2_txt}
        """

        color = color_by_zona.get(zona, "#3186cc")
        folium.CircleMarker(
            location=[lat, lon],
            radius=6,
            color=color,
            fill=True,
            fill_opacity=0.9,
            popup=folium.Popup(popup_html, max_width=300),
            tooltip=desarrollo
        ).add_to(cluster)

    # Leyenda simple por Zona
    legend_html = """
    <div style="
        position: fixed; bottom: 20px; left: 20px; z-index: 9999;
        background: white; padding: 10px 12px; border: 1px solid #ccc; border-radius: 8px;
        font-size: 13px;">
        <b>Zonas</b><br>
    """
    for z, c in color_by_zona.items():
        legend_html += f'<span style="display:inline-block;width:12px;height:12px;background:{c};margin-right:6px;border-radius:2px;"></span>{z}<br>'
    legend_html += "</div>"
    m.get_root().html.add_child(folium.Element(legend_html))

    m.save(archivo_html)
    return m

# ==== 3) Uso ====
m = make_folium_map(df, "mapa_desarrollos.html")
# Abre "mapa_desarrollos.html" en tu navegador



In [10]:
m


In [1]:
# ============================================
# Modelo log-lineal con estacionalidad (mensual)
# Entrena: 2022-01 a 2025-08
# Predice: 2025-09 a 2027-12
# - y = visitantes
# - x = turistas
# - Dummies por mes (estacionalidad)
# - Corrección de sesgo por log-normal
# - Calibración opcional en sep-dic 2025
# ============================================

import pandas as pd
import numpy as np
from sklearn.linear_model import LinearRegression

# -------------------------
# 1) Datos (turistas + visitantes) 2022-2027
#    (Pega aquí la tabla completa que compartiste: turistas y visitantes)
# -------------------------
raw = [
    # 2022
    ("ene-22", 252670,  47555),("feb-22", 187397,  33752),("mar-22", 195151,  50401),("abr-22", 259592,  88518),
    ("may-22", 286375,  52899),("jun-22", 269962,  74406),("jul-22", 278759, 117898),("ago-22", 280636, 106035),
    ("sep-22", 278508,  48593),("oct-22", 203882,  45272),("nov-22", 216805,  45395),("dic-22", 215150,  60313),
    # 2023 (enero-abril sin registro; dejaremos NaN)
    ("ene-23", 199069,      0),("feb-23", 191296,      0),("mar-23", 206714,      0),("abr-23", 220838,      0),
    ("may-23", 246132,  65396),("jun-23", 241114,  95181),("jul-23", 236356, 165041),("ago-23", 252871, 140610),
    ("sep-23", 247014,  57745),("oct-23", 198486,  49379),("nov-23", 224430,  53081),("dic-23", 237070,  72613),
    # 2024
    ("ene-24", 223116,  49328),("feb-24", 186327,  43293),("mar-24", 191706,  70971),("abr-24", 240656,  76619),
    ("may-24", 232581,  58704),("jun-24", 233522,  69427),("jul-24", 245496, 123249),("ago-24", 277021,  97003),
    ("sep-24", 254396,  36239),("oct-24", 169104,  23176),("nov-24", 151484,  24855),("dic-24", 160698,  31070),
    # 2025 (interna)
    ("ene-25", 159184,  23727),("feb-25", 111926,  20156),("mar-25", 119146,  29739),("abr-25", 148154,  43406),
    ("may-25", 173372,  38977),("jun-25", 165415,  50204),("jul-25", 180548,  93354),("ago-25", 208976,  78757),
    ("sep-25", 191711,  34471),("oct-25", 153369,  32263),("nov-25", 134198,  37575),("dic-25", 153369,  54967),
    # 2026 (interna)
    ("ene-26", 146496,  28473),("feb-26", 103005,  24188),("mar-26", 109649,  35687),("abr-26", 136345,  52088),
    ("may-26", 159553,  46773),("jun-26", 152230,  60245),("jul-26", 166157, 112025),("ago-26", 192319,  94508),
    ("sep-26", 176430,  41365),("oct-26", 141144,  38715),("nov-26", 123501,  45090),("dic-26", 141144,  65960),
    # 2027 (interna)
    ("ene-27", 133895,  34167),("feb-27",  94145,  29025),("mar-27", 100218,  42824),("abr-27", 124617,  62505),
    ("may-27", 145829,  56127),("jun-27", 139136,  72294),("jul-27", 151865, 134430),("ago-27", 175777, 113410),
    ("sep-27", 161255,  49638),("oct-27", 129004,  46458),("nov-27", 112878,  54108),("dic-27", 129004,  79152),
]

MES_MAP = {"ene":1,"feb":2,"mar":3,"abr":4,"may":5,"jun":6,"jul":7,"ago":8,"sep":9,"oct":10,"nov":11,"dic":12}
def parse_fecha(s):
    s = s.strip().lower()
    m_abbr, yy = s.split("-")
    year = 2000 + int(yy)
    month = MES_MAP[m_abbr]
    return pd.Timestamp(year, month, 1)

base = pd.DataFrame([{"fecha": parse_fecha(f), "turistas": t, "visitantes_interna": v} for f, t, v in raw]
                   ).sort_values("fecha").reset_index(drop=True)

# 2) Preparar target de entrenamiento hasta 2025-08
df = base.copy()
# Los meses sin registro real en 2023-01..04 son 0 → tratarlos como NaN para no sesgar
mask_sin_reg_2023 = df["fecha"].between(pd.Timestamp(2023,1,1), pd.Timestamp(2023,4,1))
df.loc[mask_sin_reg_2023, "visitantes_interna"] = np.where(df.loc[mask_sin_reg_2023, "visitantes_interna"]==0, np.nan, df.loc[mask_sin_reg_2023, "visitantes_interna"])

# Split
corte_train = pd.Timestamp(2025,8,1)
train = df[df["fecha"] <= corte_train].dropna(subset=["visitantes_interna"]).copy()  # ene-22..ago-25
future = df[(df["fecha"] > corte_train) & (df["fecha"] <= pd.Timestamp(2027,12,1))].copy()  # sep-25..dic-27

# 3) Features: log(turistas) + dummies mensuales
def design_matrix(x: pd.DataFrame):
    X = pd.DataFrame(index=x.index)
    X["log_tur"] = np.log(np.maximum(x["turistas"].values, 1.0))  # evitar log(0)
    X["mes"] = x["fecha"].dt.month.astype("int")
    X = pd.get_dummies(X, columns=["mes"], drop_first=True, prefix="m")  # 11 dummies
    return X

X_train = design_matrix(train)
y_train = np.log(np.maximum(train["visitantes_interna"].values, 1.0))

# 4) Ajustar regresión lineal
reg = LinearRegression()
reg.fit(X_train, y_train)

# 5) Pronóstico en el horizonte futuro
X_fut = design_matrix(future)
yhat_log = reg.predict(X_fut)

# 6) Corrección de sesgo log-normal
resid = y_train - reg.predict(X_train)
sigma2 = float(np.var(resid, ddof=X_train.shape[1])) if len(resid) > X_train.shape[1] else float(np.var(resid))
yhat = np.exp(yhat_log + 0.5 * sigma2)  # bias correction

future["pred_sin_cal"] = yhat

# 7) (Opcional) Calibración mínima en sep-dic 2025
cal_win = (future["fecha"] >= pd.Timestamp(2025,9,1)) & (future["fecha"] <= pd.Timestamp(2025,12,1))
if future.loc[cal_win, "visitantes_interna"].notna().any():
    y_true = future.loc[cal_win, "visitantes_interna"].values.astype(float)
    y_pred = future.loc[cal_win, "pred_sin_cal"].values.astype(float)
    # factor que minimiza SSE: argmin_c ||y_true - c*y_pred||^2
    cal_factor = (y_true @ y_pred) / (y_pred @ y_pred)
else:
    cal_factor = 1.0

future["pred_cal"] = future["pred_sin_cal"] * cal_factor

# 8) Métricas vs interna (en todo el horizonte futuro)
mask_eval = future["visitantes_interna"].notna()
y_true_all = future.loc[mask_eval, "visitantes_interna"].values.astype(float)
y_pred_all = future.loc[mask_eval, "pred_cal"].values.astype(float)

mape = np.mean(np.abs((y_true_all - y_pred_all) / np.where(y_true_all==0, np.nan, y_true_all))) * 100
rmse = np.sqrt(np.mean((y_true_all - y_pred_all)**2))

print(f"Calibración multiplicativa: {cal_factor:0.3f}")
print(f"MAPE (sep-2025..dic-2027): {mape:0.2f}% | RMSE: {rmse:,.0f}")




Calibración multiplicativa: 1.308
MAPE (sep-2025..dic-2027): 20.87% | RMSE: 16,714


In [2]:
# 9) Resultado: tabla completa de pronóstico vs interna
out = future[["fecha","turistas","visitantes_interna","pred_sin_cal","pred_cal"]].copy()
out["error_%_cal"] = (out["pred_cal"] - out["visitantes_interna"]) / out["visitantes_interna"] * 100
print("\nPronóstico (primeras 6 filas):")
print(out.head(6).round(0))




Pronóstico (primeras 6 filas):
        fecha  turistas  visitantes_interna  pred_sin_cal  pred_cal  \
44 2025-09-01    191711             34471.0       32012.0   41878.0   
45 2025-10-01    153369             32263.0       28748.0   37608.0   
46 2025-11-01    134198             37575.0       24542.0   32105.0   
47 2025-12-01    153369             54967.0       36670.0   47972.0   
48 2026-01-01    146496             28473.0       24649.0   32246.0   
49 2026-02-01    103005             24188.0       18076.0   23647.0   

    error_%_cal  
44         21.0  
45         17.0  
46        -15.0  
47        -13.0  
48         13.0  
49         -2.0  


In [3]:
out

fecha  turistas  visitantes_interna  pred_sin_cal       pred_cal  \
44 2025-09-01    191711             34471.0  32011.574822   41877.623974   
45 2025-10-01    153369             32263.0  28747.756214   37607.888133   
46 2025-11-01    134198             37575.0  24541.608631   32105.395118   
47 2025-12-01    153369             54967.0  36669.904799   47971.663153   
48 2026-01-01    146496             28473.0  24649.381192   32246.383457   
49 2026-02-01    103005             24188.0  18075.890940   23646.926713   
50 2026-03-01    109649             35687.0  28417.466356   37175.802097   
51 2026-04-01    136345             52088.0  38584.460672   50476.290038   
52 2026-05-01    159553             46773.0  33362.965248   43645.516383   
53 2026-06-01    152230             60245.0  43400.272854   56776.347840   
54 2026-07-01    166157            112025.0  80405.927875  105187.240292   
55 2026-08-01    192319             94508.0  73523.367311   96183.456976   
56 2026-09-01    176430             41365.0  28723.867028   37576.636239   
57 2026-10-01    141144             38715.0  25795.210845   33745.360738   
58 2026-11-01    123501             45090.0  22021.029924   28807.967612   
59 2026-12-01    141144             65960.0  32903.713212   43044.721697   
60 2027-01-01    133895             34167.0  21920.234599   28676.106912   
61 2027-02-01     94145             29025.0  16074.569819   21028.793309   
62 2027-03-01    100218             42824.0  25271.309405   33059.991535   
63 2027-04-01    124617             62505.0  34312.387359   44887.552815   
64 2027-05-01    145829             56127.0  29669.091697   38813.181565   
65 2027-06-01    139136             72294.0  38595.130636   50490.248512   
66 2027-07-01    151865            134430.0  71503.589480   93541.178456   
67 2027-08-01    175777            113410.0  65383.206263   85534.477495   
68 2027-09-01    161255             49638.0  25543.764741   33416.418302   
69 2027-10-01    129004             46458.0  22939.348544   30009.314378   
70 2027-11-01    112878             54108.0  19582.904925   25618.406259   
71 2027-12-01    129004             79152.0  29260.848081   38279.116224   

    error_%_cal  
44    21.486536  
45    16.566619  
46   -14.556500  
47   -12.726430  
48    13.252497  
49    -2.236949  
50     4.171833  
51    -3.094206  
52    -6.686515  
53    -5.757577  
54    -6.103780  
55     1.772820  
56    -9.158380  
57   -12.836470  
58   -36.110074  
59   -34.741174  
60   -16.070750  
61   -27.549377  
62   -22.800319  
63   -28.185661  
64   -30.847575  
65   -30.159836  
66   -30.416441  
67   -24.579422  
68   -32.679765  
69   -35.405497  
70   -52.653201  
71   -51.638473

In [ ]:
# (Opcional) totales anuales
out["anio"] = out["fecha"].dt.year
totales_anuales = out.groupby("anio")[["visitantes_interna","pred_cal"]].sum().round(0)
print("\nTotales anuales (interna vs modelo calibrado):")
print(totales_anuales)